In [1]:
import pandas
from matplotlib import pyplot as plt
import numpy as np

In [2]:
class PatientData:
    def __init__(self, number, gender, age, weight, height):
        self.n = number
        self.gender = gender
        self.age = age
        self.weight=weight
        self.height=height 
        self.symptom_list = []
        self.responses = {}
        
    def add_symptom(self, s):
        self.symptom_list.append(s)
        
    def add_response(self, resp_id, diag, pct, reasoning):
        assert resp_id not in self.responses
        self.responses[resp_id] = (diag, pct, reasoning)
        
    def get_top_symptom(self):
        if 1 not in self.responses:
            return None
        return self.responses[1][0]
    
    def get_top_three_symptoms(self, k = 3):
        lst = [v[0] for (i, v) in self.responses.items() if i <= k]
        return lst

    

In [3]:
import re
def process_file(filename):
    file = open(filename,'r')
    cur_patient = None
    all_patients = []
    for line in file:
        m = re.match('\s*P:\s*(\d+),\s*(male|female)\s*,\s*(\d+)\s*,\s*(\d+)\s*,\s*(\d+)\s*', line)
        if m:
            print(f'Patient: number {m.group(1)}, gender {m.group(2)}, age {m.group(3)}, weight {m.group(4)}, height {m.group(5)}')
            if cur_patient != None:
                all_patients.append(cur_patient)
            cur_patient = PatientData(int(m.group(1)), m.group(2), int(m.group(3)), float(m.group(4)), float(m.group(5)))
        else:
            m = re.match('s*S:\s*(.*)', line)
            if m:
                print(f'Symptom: {m.group(1)}')
                assert cur_patient != None
                cur_patient.add_symptom(m.group(1))
            else:
                m = re.match('\s*R:\s*(\d+)\s*,\s*(.*)\s*,\s*(\d+)\s*,\s*(.*)', line)
                if m:
                    resp_id = int(m.group(1))
                    diag = m.group(2).strip()
                    pct = int(m.group(3))
                    reasoning = m.group(4).strip()
                    print(f'response: {resp_id},*{diag}*,{pct}%,*{reasoning}*')
                    assert cur_patient != None
                    cur_patient.add_response(resp_id, diag, pct, reasoning)
    return all_patients

Patient: number 1, gender female, age 10, weight 54, height 46
Symptom: Progressive proximal muscles weakness
Symptom: Easy fatigue
Symptom: Gottron Papule
Symptom: Helioptrope rash
Symptom: Malar rash
Symptom: Muscle pain or tenderness
Symptom: Weight loss
Symptom: Falling episodes
Symptom: Arthritis
Symptom: Lymphadenopathy
Symptom: Cutaneous ulceration
response: 1,*Juvenile Dermatomyositis*,80%,*The patient presents with a combination of progressive proximal muscle weakness, Gottron papules, heliotrope rash, malar rash, muscle pain/tenderness, weight loss, falling episodes, and cutaneous ulceration, which are all classic features of Juvenile Dermatomyositis.*
response: 2,*Systemic Lupus Erythematosus*,60%,*The patient's symptoms of malar rash, arthritis, lymphadenopathy, and cutaneous ulceration are consistent with Systemic Lupus Erythematosus.*
response: 3,*Polymyositis*,50%,*The patient's symptoms of progressive proximal muscle weakness, muscle pain/tenderness, and weight loss are

In [8]:
def print_csv_with_symptoms(outfilename, patients_list, k=50):
    fhandle = open(outfilename+'.csv', 'w')
    for i in range(k):
        p = patients_list[i]
        print(i+1, file=fhandle, end=',')
        symptom_list_str = ','.join(p.symptom_list)
        print(f'\"{symptom_list_str}\"', file=fhandle)
    fhandle.close()

In [9]:
filename='JDM-formal-chatgpt-3.5.txt'
all_patients_jdm = process_file(filename)
print_csv_with_symptoms('jdm-formal-50',all_patients_jdm,k=50)

Patient: number 1, gender female, age 10, weight 54, height 46
Symptom: Progressive proximal muscles weakness
Symptom: Easy fatigue
Symptom: Gottron Papule
Symptom: Helioptrope rash
Symptom: Malar rash
Symptom: Muscle pain or tenderness
Symptom: Weight loss
Symptom: Falling episodes
Symptom: Arthritis
Symptom: Lymphadenopathy
Symptom: Cutaneous ulceration
response: 1,*Juvenile Dermatomyositis*,80%,*The patient presents with a combination of progressive proximal muscle weakness, Gottron papules, heliotrope rash, malar rash, muscle pain/tenderness, weight loss, falling episodes, and cutaneous ulceration, which are all classic features of Juvenile Dermatomyositis.*
response: 2,*Systemic Lupus Erythematosus*,60%,*The patient's symptoms of malar rash, arthritis, lymphadenopathy, and cutaneous ulceration are consistent with Systemic Lupus Erythematosus.*
response: 3,*Polymyositis*,50%,*The patient's symptoms of progressive proximal muscle weakness, muscle pain/tenderness, and weight loss are

In [10]:
filename='JDM-informal-chatgpt-3.5.txt'
all_patients_jdm = process_file(filename)
print_csv_with_symptoms('jdm-informal-50',all_patients_jdm,k=50)

Patient: number 1, gender female, age 10, weight 54, height 46
Symptom: Cannot raise arms
Symptom: Tired
Symptom: rash on hands
Symptom: Dark eyelids
Symptom: Rash on cheeks
Symptom: Musculoskeletal pain
Symptom: Fever
Symptom: Stuck joint
Symptom: Cannot  tolerate sun
Symptom: Tender gums
response: 1,*Juvenile Dermatomyositis*,60%,*The patient presents with inability to raise arms, musculoskeletal pain, rash on hands and cheeks, tiredness, dark eyelids, fever, and sun intolerance, which are all characteristic symptoms of Juvenile Dermatomyositis.*
response: 2,*Systemic Lupus Erythematosus*,30%,*The patient's symptoms of rash on cheeks, tiredness, musculoskeletal pain, fever, and sun intolerance are consistent with Systemic Lupus Erythematosus.*
response: 3,*Juvenile Idiopathic Arthritis*,20%,*The symptoms of musculoskeletal pain, stuck joint, fever, and tender gums are suggestive of Juvenile Idiopathic Arthritis.*
response: 4,*Juvenile Scleroderma*,10%,*The combination of musculoskele

In [11]:
filename='SLE-formal-chatgpt-3.5.txt'
all_patients_sle = process_file(filename)
print_csv_with_symptoms('SLE-formal-50',all_patients_sle,k=50)

Patient: number 1, gender female, age 10, weight 54, height 46
Symptom: Arthritis
Symptom: Malar rash
Symptom: Photosensitive rash
Symptom: Nephritis
Symptom: Pericardiitis 
response: 1,*Systemic Lupus Erythematosus (SLE)*,80%,*The patient presents with malar rash, photosensitive rash, arthritis, nephritis, and pericarditis, which are all characteristic features of SLE in children.*
response: 2,*Juvenile Idiopathic Arthritis (JIA)*,15%,*Arthritis is a common symptom in JIA, which is a possibility given the patient's age and presentation with joint symptoms.*
response: 3,*Systemic Juvenile Idiopathic Arthritis (SJIA)*,5%,*SJIA can present with arthritis along with systemic symptoms like rash and inflammation of internal organs, which align with the patient's symptoms.*
response: 4,*Kawasaki Disease*,5%,*Kawasaki disease can present with symptoms like rash, arthritis, and inflammation of blood vessels, which may be considered in this case.*
response: 5,*Systemic Sclerosis*,2%,*Although l

In [12]:
filename='SLE-informal-chatgpt-3.5.txt'
all_patients_sle = process_file(filename)
print_csv_with_symptoms('SLE-informal-50',all_patients_sle,k=50)

Patient: number 1, gender female, age 10, weight 54, height 46
Symptom: lumps in neck
Symptom: Butterfly rash
Symptom: Lung disease
response: 1,*Systemic Lupus Erythematosus (SLE)*,70%,*The patient presents with a butterfly rash, which is a common skin manifestation of SLE. Additionally, the presence of lumps in the neck could be related to lymphadenopathy, a common feature of SLE.*
response: 2,*Lymphoma*,20%,*Lumps in the neck can be a sign of lymphoma, and the presence of lung disease can also be associated with certain types of lymphoma.*
response: 3,*Tuberculosis*,5%,*The combination of lumps in the neck and lung disease could be indicative of tuberculosis, especially in a child with these symptoms.*
response: 4,*Sarcoidosis*,3%,*Sarcoidosis can present with lumps in the neck and lung disease, although it is less common in children.*
response: 5,*Kawasaki disease*,2%,*Kawasaki disease can present with a rash and lymphadenopathy, which could be mistaken for lumps in the neck.*
Patie

In [13]:
filename='MCTD-formal-chatgpt-3.5.txt'
all_patients_mctd = process_file(filename)
print_csv_with_symptoms('MCTD-formal-50',all_patients_mctd,k=50)

Patient: number 1, gender female, age 10, weight 54, height 46
Symptom: Arthritis
Symptom: Gottron's papules
Symptom: Abnormal esophageal motility
Symptom: Cardiac disease
Symptom: Muscle disease
response: 1,*Juvenile Idiopathic Arthritis*,40%,*The patient presents with arthritis which is common in Juvenile Idiopathic Arthritis.*
response: 2,*Juvenile Dermatomyositis*,30%,*Gottron's papules and muscle weakness are characteristic features of Juvenile Dermatomyositis.*
response: 3,*Eosinophilic Esophagitis*,15%,*Abnormal esophageal motility can be seen in Eosinophilic Esophagitis.*
response: 4,*Juvenile Rheumatic Heart Disease*,10%,*Cardiac disease can be associated with Juvenile Rheumatic Heart Disease.*
response: 5,*Duchenne Muscular Dystrophy*,5%,*Muscle weakness can be a symptom of Duchenne Muscular Dystrophy.*
Patient: number 2, gender female, age 10, weight 54, height 46
Symptom: Arthritis
Symptom: Raynaud's phenomenon
Symptom: Malar rash
Symptom: Gottron's papules
Symptom: Fever
S

In [14]:
filename='MCTD-informal-chatgpt-3.5.txt'
all_patients_mctd = process_file(filename)
print_csv_with_symptoms('MCTD-informal-50',all_patients_mctd,k=50)

Patient: number 1, gender female, age 10, weight 54, height 46
Symptom: Joint tenderness
Symptom: Fingers turning white
Symptom: Fever
Symptom: Cardiac disease
Symptom: Chest pain
Symptom: Abnormal lung  diffusion
Symptom: Restrictive lung disese
response: 1,*Juvenile Idiopathic Arthritis*,40%,*The patient presents with joint tenderness which is consistent with arthritis. This condition commonly affects children and can cause joint pain and tenderness.*
response: 2,*Raynaud's Phenomenon*,30%,*The symptoms of fingers turning white suggest possible Raynaud's Phenomenon, a condition characterized by vasospasm of small arteries, leading to color changes in the fingers in response to cold or stress.*
response: 3,*Systemic Lupus Erythematosus (SLE)*,15%,*Fever, joint tenderness, and cardiac disease can be seen in SLE, an autoimmune disease that can affect multiple organs.*
response: 4,*Myocarditis*,10%,*The presence of cardiac disease, chest pain, and fever raises concern for myocarditis, wh

In [15]:
filename='SystemicSclerosis-formal-chatgpt-3.5.txt'
all_patients_ss = process_file(filename)
print_csv_with_symptoms('SystemicSclerosis-formal-50',all_patients_ss,k=50)

Patient: number 1, gender female, age 10, weight 54, height 46
Symptom: Skin tightening 
Symptom: Rayanud phenomenon
Symptom: Soft tissue contracture
Symptom: Artharlgia
Symptom: Muscle weakness and pain
Symptom: Dyspnea 
response: 1,*Juvenile Systemic Sclerosis*,70%,*The patient presents with skin tightening, Raynaud phenomenon, soft tissue contracture, and dyspnea, which are all characteristic symptoms of juvenile systemic sclerosis.*
response: 2,*Juvenile Dermatomyositis*,15%,*Muscle weakness and pain along with arthralgia are common symptoms of juvenile dermatomyositis in children.*
response: 3,*Mixed Connective Tissue Disease*,10%,*The combination of skin tightening, Raynaud phenomenon, soft tissue contracture, and dyspnea could also be seen in mixed connective tissue disease.*
response: 4,*Juvenile Idiopathic Arthritis*,3%,*Arthralgia and muscle weakness are common symptoms in juvenile idiopathic arthritis, but the presence of skin tightening and other symptoms make this less lik

In [16]:
filename='SystemicSclerosis-informal-chatgpt-3.5.txt'
all_patients_ss = process_file(filename)
print_csv_with_symptoms('SystemicSclerosis-informal-50',all_patients_ss,k=50)

Patient: number 1, gender female, age 10, weight 54, height 46
Symptom: shiny skin
Symptom: Cold hands
Symptom: Tight joint
Symptom: Tender muscles
response: 1,*Juvenile Idiopathic Arthritis*,70%,*The symptoms of tight joints and tender muscles are consistent with juvenile idiopathic arthritis, which is common in children and can cause inflammation in the joints leading to stiffness and pain.*
response: 2,*Hypothyroidism*,20%,*Shiny skin and cold hands can be indicative of hypothyroidism, a condition where the thyroid gland does not produce enough hormones, leading to a slower metabolism and symptoms like cold intolerance and changes in skin texture.*
response: 3,*Juvenile Dermatomyositis*,5%,*The combination of shiny skin, tender muscles, and joint tightness could be seen in juvenile dermatomyositis, an autoimmune condition that affects the skin and muscles in children.*
response: 4,*Systemic Lupus Erythematosus (SLE)*,3%,*SLE is a chronic autoimmune disease that can cause joint pain 